In [388]:
import requests
import json
import pandas as pd
import time
from dotenv import load_dotenv
import os

In [389]:
load_dotenv()
API_KEY = os.getenv('API_KEY')

In [390]:
url = 'https://v3.football.api-sports.io/status'

headers = {
    'x-apisports-key': API_KEY,
}

response = requests.get(url, headers=headers)
response.json()

{'get': 'status',
 'parameters': [],
 'errors': [],
 'results': 0,
 'paging': {'current': 1, 'total': 1},
 'response': {'account': {'firstname': 'Климентий',
   'lastname': 'Пролецкий',
   'email': 'klimentiy.proletskiy@gmail.com'},
  'subscription': {'plan': 'Pro',
   'end': '2025-12-10T22:44:05+00:00',
   'active': True},
  'requests': {'current': 2471, 'limit_day': 7500}}}

In [391]:
def call_api(endpoint, params = {}):
    url = f"https://v3.football.api-sports.io/{endpoint}"
    headers = {
        "x-rapidapi-key": API_KEY
    }
    try:
        response = requests.get(
            url,
            params=params,
            headers=headers
        )
        return response.json()
    except requests.exceptions.RequestException as e:
        print(f"Ошибка запроса: {e}")
        return None

In [392]:
leagues = call_api('leagues')

In [393]:
leagues['response']

[{'league': {'id': 4,
   'name': 'Euro Championship',
   'type': 'Cup',
   'logo': 'https://media.api-sports.io/football/leagues/4.png'},
  'country': {'name': 'World', 'code': None, 'flag': None},
  'seasons': [{'year': 2008,
    'start': '2008-06-07',
    'end': '2008-06-29',
    'current': False,
    'coverage': {'fixtures': {'events': True,
      'lineups': True,
      'statistics_fixtures': False,
      'statistics_players': False},
     'standings': False,
     'players': True,
     'top_scorers': True,
     'top_assists': True,
     'top_cards': True,
     'injuries': False,
     'predictions': True,
     'odds': False}},
   {'year': 2012,
    'start': '2012-06-08',
    'end': '2012-07-01',
    'current': False,
    'coverage': {'fixtures': {'events': True,
      'lineups': True,
      'statistics_fixtures': False,
      'statistics_players': False},
     'standings': False,
     'players': True,
     'top_scorers': True,
     'top_assists': True,
     'top_cards': True,
     'i

In [394]:
def clean_leagues_columns(leagues_df):
    leagues_df['league_id'] = leagues_df['league'].apply(lambda d: d['id'])
    leagues_df['league_name'] = leagues_df['league'].apply(lambda d: d['name'])
    leagues_df['league_country'] = leagues_df['country'].apply(lambda d: d['name'])
    return leagues_df[['league_id', 'league_name', 'league_country']]

In [395]:
leagues_df = pd.DataFrame(leagues['response'])
leagues_df_cleaned = clean_leagues_columns(leagues_df)
leagues_sorted = leagues_df_cleaned.sort_values('league_id')
leagues_sorted.head()

league_id            league_name league_country
14           1              World Cup          World
116          2  UEFA Champions League          World
179          3     UEFA Europa League          World
0            4      Euro Championship          World
395          5    UEFA Nations League          World

In [396]:
leagues_sorted.to_csv('Leagues_list', index=False)

In [397]:
leagues_list = [39, 40, 140, 135, 78, 61, 144, 94, 253, 235, 71, 119, 128, 88, 262, 106, 136, 218, 141, 113]
most_popular_leagues = leagues_sorted[leagues_sorted['league_id'].isin(leagues_list)]
most_popular_leagues

league_id                 league_name league_country
6           39              Premier League        England
19          40                Championship        England
3           61                     Ligue 1         France
5           71                     Serie A         Brazil
7           78                  Bundesliga        Germany
9           88                  Eredivisie    Netherlands
10          94               Primeira Liga       Portugal
393        106                 Ekstraklasa         Poland
217        113                 Allsvenskan         Sweden
89         119                   Superliga        Denmark
191        128  Liga Profesional Argentina      Argentina
8          135                     Serie A          Italy
213        136                     Serie B          Italy
11         140                     La Liga          Spain
212        141            Segunda División          Spain
4          144          Jupiler Pro League        Belgium
74         218                  Bundesliga        Austria
225        235              Premier League         Russia
129        253         Major League Soccer            USA
252        262                     Liga MX         Mexico

In [398]:
def players_data(league, season, page = 1, players_data_list = None):
    if players_data_list is None:
        players_data_list = []
    players = call_api('players', {'league': league, 'season': season, 'page': page})
    if 'response' in players:
        players_ids = []
        for player_data in players['response']:
            if 'player' in player_data and 'id' in player_data['player']:
                player_id = player_data['player']['id']
                players_ids.append(str(player_id))
        player_ids_str = "-".join(players_ids)
        players_trophies = call_api('trophies', {'players': player_ids_str})
        for i in range(len(players['response'])):
            for j in range(len(players_trophies['response'])):
                if players['response'][i]['player']['id'] == players_trophies['response'][j]['id']:
                    players['response'][i]['trophies'] = players_trophies['response'][j]['trophies']
        
        players_sidelined_reason_list = call_api('sidelined', {'players': player_ids_str})
        for i in range(len(players['response'])):
            for j in range(len(players_sidelined_reason_list['response'])):
                if players['response'][i]['player']['id'] == players_sidelined_reason_list['response'][j]['id']:
                    players['response'][i]['sidelined'] = players_sidelined_reason_list['response'][j]['sidelined']

        players_data_list.extend(players['response'])
    
        paging = players.get('paging', {})
        current_page = paging.get('current', 1)
        total_pages = paging.get('total', 1)
        if current_page < total_pages:
            next_page = current_page + 1
            if next_page % 2 == 1:
                time.sleep(1)
            players_data_list = players_data(league, season, next_page, players_data_list)

    return players_data_list

players = []
for league in leagues_list:
    players_league = players_data(league, 2024)
    players.extend(players_league)
print(len(players))

18955


In [399]:
def clean_players_stats_df(players):
    players_stats_df = pd.DataFrame(players)
    players_stats_df['player_id'] = players['player'].apply(lambda d: d['id'])
    players_stats_df['player_name'] = players['player'].apply(lambda d: d['name'])
    players_stats_df['age'] = players['player'].apply(lambda d: d['age'])
    players_stats_df['country_birth'] = players['player'].apply(lambda d: d['birth']['country'])
    players_stats_df['nationality'] = players['player'].apply(lambda d: d['nationality'])
    players_stats_df['player_height'] = players['player'].apply(lambda d: d['height'])
    players_stats_df['player_weight'] = players['player'].apply(lambda d: d['weight'])
    players_stats_df['player_photo'] = players['player'].apply(lambda d: d['photo'])
    players_stats_df['injured'] = players['player'].apply(lambda d: d['injured'])
    players_stats_df['team_id'] = players['statistics'].apply(lambda stats: [team_dict['team']['id'] for team_dict in stats][0])
    # players_stats_df['team'] = players['statistics'].apply(lambda stats: ', '.join([team_dict['team']['name'] for team_dict in stats]))
    players_stats_df['league'] = players['statistics'].apply(lambda d: d[0]['league']['country'] + d[0]['league']['name'])
    players_stats_df['season'] = players['statistics'].apply(lambda d: d[0]['league']['season'])
    players_stats_df['position'] = players['statistics'].apply(lambda d: d[0]['games']['position'])
    players_stats_df['is_captain'] = players['statistics'].apply(lambda d: d[0]['games']['captain'])
    players_stats_df['shots_on'] = players['statistics'].apply(lambda d: d[0]['shots']['on'])
    players_stats_df['shots_total'] = players['statistics'].apply(lambda d: d[0]['shots']['total'])
    players_stats_df['goals'] = players['statistics'].apply(lambda d: d[0]['goals']['total'])
    players_stats_df['assists'] = players['statistics'].apply(lambda d: d[0]['goals']['assists'])
    players_stats_df['passes_total'] = players['statistics'].apply(lambda d: d[0]['passes']['total'])
    players_stats_df['passes_key'] = players['statistics'].apply(lambda d: d[0]['passes']['key'])
    players_stats_df['duels_total'] = players['statistics'].apply(lambda d: d[0]['duels']['total'])
    players_stats_df['duels_won'] = players['statistics'].apply(lambda d: d[0]['duels']['won'])
    players_stats_df['dribbles_attempts'] = players['statistics'].apply(lambda d: d[0]['dribbles']['attempts'])
    players_stats_df['dribbles_success'] = players['statistics'].apply(lambda d: d[0]['dribbles']['success'])
    players_stats_df['fouls'] = players['statistics'].apply(lambda d: d[0]['fouls']['drawn'])
    players_stats_df['yellow_cards'] = players['statistics'].apply(lambda d: d[0]['cards']['yellow'])
    players_stats_df['yellow_red_cards'] = players['statistics'].apply(lambda d: d[0]['cards']['yellowred'])
    players_stats_df['red_cards'] = players['statistics'].apply(lambda d: d[0]['cards']['red'])
    players_stats_df['sidelined_times'] = players['sidelined'].apply(lambda d: len(d) if isinstance(d, list) else 0)
    players_stats_df['trophies_count'] = players['trophies'].apply(lambda d: len(d) if isinstance(d, list) else 0)
    players_stats_df['player_rating'] = players['statistics'].apply(lambda d: d[0]['games']['rating'])
    return players_stats_df.iloc[:, 4:]

In [400]:
players_stats_df = pd.DataFrame(players)
cleaned_players_stats_df = clean_players_stats_df(players_stats_df)
cleaned_players_stats_df

player_id     player_name   age country_birth  nationality  \
0             83      A. Danjuma  28.0       Nigeria  Netherlands   
1            105  F. Ballo-Touré  28.0        France      Senegal   
2            172         D. Alli  29.0       England      England   
3           2699      S. Ghoddos  32.0        Sweden         Iran   
4          18765     André Gomes  32.0      Portugal     Portugal   
...          ...             ...   ...           ...          ...   
18950     152955    L. Bergström  23.0       Finland      Finland   
18951     287111   Fabian Mrozek  22.0        Poland       Poland   
18952     347316     L. Bergvall  19.0        Sweden       Sweden   
18953     410125     M. Yalcouyé  20.0          Mali         Mali   
18954     415517     Lamine Dabo  21.0         Spain        Spain   

      player_height player_weight  \
0               178            74   
1               182            70   
2               188            76   
3               175            79   
4               188            84   
...             ...           ...   
18950           205            82   
18951           192          None   
18952           187            74   
18953           169          None   
18954           185          None   

                                            player_photo  injured  team_id  \
0      https://media.api-sports.io/football/players/8...    False       45   
1      https://media.api-sports.io/football/players/1...    False       36   
2      https://media.api-sports.io/football/players/1...    False       45   
3      https://media.api-sports.io/football/players/2...    False       55   
4      https://media.api-sports.io/football/players/1...    False       45   
...                                                  ...      ...      ...   
18950  https://media.api-sports.io/football/players/1...    False      371   
18951  https://media.api-sports.io/football/players/2...    False      371   
18952  https://media.api-sports.io/football/players/3...    False      364   
18953  https://media.api-sports.io/football/players/4...    False      366   
18954  https://media.api-sports.io/football/players/4...    False      377   

       ... duels_won  dribbles_attempts dribbles_success  fouls  yellow_cards  \
0      ...       NaN                NaN              NaN    NaN           NaN   
1      ...       NaN                NaN              NaN    NaN           NaN   
2      ...       NaN                NaN              NaN    NaN           NaN   
3      ...       NaN                NaN              NaN    NaN           NaN   
4      ...       NaN                NaN              NaN    NaN           NaN   
...    ...       ...                ...              ...    ...           ...   
18950  ...       3.0                NaN              NaN    2.0           0.0   
18951  ...       1.0                NaN              NaN    NaN           0.0   
18952  ...      65.0               32.0             20.0   17.0           2.0   
18953  ...      96.0               43.0             15.0   54.0           3.0   
18954  ...     122.0               28.0             17.0   34.0           2.0   

       yellow_red_cards  red_cards  sidelined_times  trophies_count  \
0                   NaN        NaN               11               8   
1                   NaN        NaN                4              14   
2                   NaN        NaN               17              12   
3                   NaN        NaN                5               2   
4                   NaN        NaN               36              35   
...                 ...        ...              ...             ...   
18950               0.0        0.0                0              21   
18951               0.0        0.0                0               8   
18952               0.0        0.0                3              10   
18953               0.0        0.0                0               4   
18954               0.0        0.0        

In [401]:
teams = []
for league in leagues_list:
    teams_league = call_api('teams', {'league': league, 'season': 2024})
    teams.extend(teams_league['response'])
teams

[{'team': {'id': 33,
   'name': 'Manchester United',
   'code': 'MUN',
   'country': 'England',
   'founded': 1878,
   'national': False,
   'logo': 'https://media.api-sports.io/football/teams/33.png'},
  'venue': {'id': 556,
   'name': 'Old Trafford',
   'address': 'Sir Matt Busby Way',
   'city': 'Manchester',
   'capacity': 76212,
   'surface': 'grass',
   'image': 'https://media.api-sports.io/football/venues/556.png'}},
 {'team': {'id': 34,
   'name': 'Newcastle',
   'code': 'NEW',
   'country': 'England',
   'founded': 1892,
   'national': False,
   'logo': 'https://media.api-sports.io/football/teams/34.png'},
  'venue': {'id': 562,
   'name': "St. James' Park",
   'address': 'St. James&apos; Street',
   'city': 'Newcastle upon Tyne',
   'capacity': 52758,
   'surface': 'grass',
   'image': 'https://media.api-sports.io/football/venues/562.png'}},
 {'team': {'id': 35,
   'name': 'Bournemouth',
   'code': 'BOU',
   'country': 'England',
   'founded': 1899,
   'national': False,
   '

In [402]:
def clean_teams_df(teams):
    teams_df = pd.DataFrame(teams)
    teams_df['team_id'] = teams_df['team'].apply(lambda d: d['id'])
    teams_df['team_name'] = teams_df['team'].apply(lambda d: d['name'])
    teams_df['team_country'] = teams_df['team'].apply(lambda d: d['country'])
    teams_df['team_logo'] = teams_df['team'].apply(lambda d: d['logo'])
    return teams_df[['team_id', 'team_name', 'team_country', 'team_logo']]

In [403]:
cleaned_teams_df = clean_teams_df(teams)
cleaned_teams_df

team_id          team_name team_country  \
0         33  Manchester United      England   
1         34          Newcastle      England   
2         35        Bournemouth      England   
3         36             Fulham      England   
4         39             Wolves      England   
..       ...                ...          ...   
391     2163        IFK Varnamo       Sweden   
392     2170               Gais       Sweden   
393     2176    Landskrona BoIS       Sweden   
394     2240        Mjallby AIF       Sweden   
395     2241     Vasteras SK FK       Sweden   

                                             team_logo  
0    https://media.api-sports.io/football/teams/33.png  
1    https://media.api-sports.io/football/teams/34.png  
2    https://media.api-sports.io/football/teams/35.png  
3    https://media.api-sports.io/football/teams/36.png  
4    https://media.api-sports.io/football/teams/39.png  
..                                                 ...  
391  https://media.api-sports.io/football/teams/216...  
392  https://media.api-sports.io/football/teams/217...  
393  https://media.api-sports.io/football/teams/217...  
394  https://media.api-sports.io/football/teams/224...  
395  https://media.api-sports.io/football/teams/224...  

[396 rows x 4 columns]

In [404]:
cleaned_teams_df = cleaned_teams_df.set_index('team_id')
cleaned_players_stats_df = cleaned_players_stats_df.set_index('team_id')

In [405]:
cleaned_players_stats_df = pd.merge(cleaned_players_stats_df, cleaned_teams_df, left_index=True, right_index=True, how='left')
cleaned_players_stats_df = cleaned_players_stats_df.reset_index()
cleaned_players_stats_df

team_id  player_id     player_name   age country_birth  nationality  \
0           45         83      A. Danjuma  28.0       Nigeria  Netherlands   
1           36        105  F. Ballo-Touré  28.0        France      Senegal   
2           45        172         D. Alli  29.0       England      England   
3           55       2699      S. Ghoddos  32.0        Sweden         Iran   
4           45      18765     André Gomes  32.0      Portugal     Portugal   
...        ...        ...             ...   ...           ...          ...   
18950      371     152955    L. Bergström  23.0       Finland      Finland   
18951      371     287111   Fabian Mrozek  22.0        Poland       Poland   
18952      364     347316     L. Bergvall  19.0        Sweden       Sweden   
18953      366     410125     M. Yalcouyé  20.0          Mali         Mali   
18954      377     415517     Lamine Dabo  21.0         Spain        Spain   

      player_height player_weight  \
0               178            74   
1               182            70   
2               188            76   
3               175            79   
4               188            84   
...             ...           ...   
18950           205            82   
18951           192          None   
18952           187            74   
18953           169          None   
18954           185          None   

                                            player_photo  injured  ... fouls  \
0      https://media.api-sports.io/football/players/8...    False  ...   NaN   
1      https://media.api-sports.io/football/players/1...    False  ...   NaN   
2      https://media.api-sports.io/football/players/1...    False  ...   NaN   
3      https://media.api-sports.io/football/players/2...    False  ...   NaN   
4      https://media.api-sports.io/football/players/1...    False  ...   NaN   
...                                                  ...      ...  ...   ...   
18950  https://media.api-sports.io/football/players/1...    False  ...   2.0   
18951  https://media.api-sports.io/football/players/2...    False  ...   NaN   
18952  https://media.api-sports.io/football/players/3...    False  ...  17.0   
18953  https://media.api-sports.io/football/players/4...    False  ...  54.0   
18954  https://media.api-sports.io/football/players/4...    False  ...  34.0   

       yellow_cards yellow_red_cards  red_cards  sidelined_times  \
0               NaN              NaN        NaN               11   
1               NaN              NaN        NaN                4   
2               NaN              NaN        NaN               17   
3               NaN              NaN        NaN                5   
4               NaN              NaN        NaN               36   
...             ...              ...        ...              ...   
18950           0.0              0.0        0.0                0   
18951           0.0              0.0        0.0                0   
18952           2.0              0.0        0.0                3   
18953           3.0              0.0        0.0                0   
18954           2.0              0.0        0.0                1   

       trophies_count  player_rating          team_name  team_country  \
0                   8           None            Everton       England   
1                  14           None             Fulham       England   
2                  12           None            Everton       England   
3                   2           None          Brentford       England   
4                  35           None            Everton       England   
...               ...            ...                ...           ...   
18950              21       6.600000  IF Brommapojkarna        Sweden   
18951               8       6.740000  IF Brommapojkarna        Sweden   
18952              10       7.325000     Djurgardens IF        Sweden   
18953               4       7.054545       IFK Goteborg        Sweden   
18954               0       7.178947      AI

In [406]:
cleaned_players_stats_df.to_csv('players_stats', index=False)